<img src="ptychoscopy/logo.png" style="height:180px">

                                    Code @ Radim Skoupý, PSI Villigen 2024

Jupyter Notebook/Lab based interactive data acquisition tool designed for appropriate ptychographic data collection. It consists of **SSB** (Single Side Band ptychography) or **full-field ITR** (iterative reconstruction methods) tabs where method related charts may be found. With this tool, you can check the probe CTF, scanning step size, probe overlap, illumination uniformity, detector camera length a proper angular range collection, reconstructed probe size and many more. For in-detail intructions and up-to-date version visit [GitLab](https://gitlab.psi.ch/em-and-diffraction/low-dose-electron-ptychography/ptychoscopy/-/wikis/ptychoScopy) repository.
 
#### Start the interactive gui by running the field called RUN ME and then
```python
display(ptychoscopy)
```

#### Check installed package versions
```python
from ptychoscopy import pty
pty.get_versions() # run before "display(ptychoscopy)" field
```

#### If you use ptychoScopy in your research, we kindly ask that you cite our paper:
Skoupy R., Mueller E., Pennycook T., Guizar-Sicairos M., Fabbri E., Poghosyan E. ptychoScopy: Users Guide for Optimal Acquisition Design with Electron Ptychography, xxxx, xx, [DOI](https://doi.org)

In [2]:
display(ptychoscopy)

## RUN ME

In [1]:
### Initial packages import
import io
import sys
import numpy as np
import ipywidgets as widg
import scipy.constants as cons
import plotly.express as px
import plotly.graph_objects as go
from ptychoscopy import pty
from IPython.display import display
from plotly.subplots import make_subplots

try:
    from abtem import Probe
    abtem = True
except:
    abtem = False

def show_probe_angle(caller):
    aperture_res.value = f'Semi-angle (mrad) {"{:.1f}".format(pty.get_angle(caller.new))}'   
    return aperture_res.value
def show_corrprobe_angle(caller):
    aperture_res2.value = f'corr. {"{:.2f}".format(pty.get_angle_corr(caller.new))}'
    return aperture_res2.value

### MICROSCOPE CONTROL PANEL
image = open("ptychoscopy/logo.png", "rb").read()
logo = widg.Image(value=image, format='png', layout=widg.Layout(grid_area='logo',width='95%',))
ali  = dict(style = {'description_width': '110px','button_width': '55px', 'font_weight': 'bold'}, button_style='', disabled = False)

ali3 = dict(style = {'description_width': '110px','button_width': '59.5px', 'font_weight': 'bold'}, button_style='', disabled = False)
method = widg.ToggleButtons(options=[('SSB ','ssb'),('ITR ','iterative')],description='',icons=['opera','refresh'], tooltips=['Single side band ptychography', 'Iterative reconstruction methods (e.g. PIE, ML, DM)'],
                          layout=widg.Layout(width='97.5%', grid_area='methods'), style = {'button_width': '48%','font_weight': 'bold'}, button_style='', disabled = False)

### Electron beam settings
beam_set      = widg.Button(description='Electron beam settings',layout=widg.Layout(width='95%',grid_area='beam_set'),style=widg.ButtonStyle(button_color='#3b446b',font_weight='bold',font_size='16px',text_color='white'),disabled=False) 
beam_energy   = widg.SelectionSlider(options=pty.load_energies(), value=200, description='Beam energy (keV)', layout=widg.Layout(width='95%', grid_area='beam_set1'), **ali)
probe_size_list = pty.load_probes()
probe_size    = widg.Dropdown(options=probe_size_list, value=probe_size_list[1], description='Probe', layout=widg.Layout(width='95%', grid_area='beam_set3'), **ali)
probe_size_ma = widg.BoundedFloatText(value=0, description='', min=0, disabled=False, layout=widg.Layout(width='75%', grid_area='beam_set5'))
defocus       = widg.FloatSlider(description='Defocus (nm)', value=0, min=0, max=2500, step=5, readout_format='d',continuous_update=False, layout=widg.Layout(width='95%', grid_area='beam_set4'), **ali)
aperture_name = widg.Label(value = 'Aperture', layout=widg.Layout(width='95%', grid_area='aperture_name'),)
aperture_list = pty.load_apertures()
aperture      = widg.Dropdown(options=aperture_list, description='Aperture', value=aperture_list[1], layout=widg.Layout(width='95%', grid_area='beam_set2'), **ali)
aperture_ma   = widg.BoundedFloatText(value=0, description='', min=0, disabled=False, layout=widg.Layout(width='75%', grid_area='beam_set6'))

### Scanning parameters
scanning_set  = widg.Button(description='Scanning parameters', layout=widg.Layout(width='95%', grid_area='scanning_set'),style=widg.ButtonStyle(button_color='#3b446b', font_weight= 'bold',font_size= '16px',text_color='white'),disabled = False)
mag           = widg.Dropdown(options=pty.load_magnifications(), value=20, description='Magnification Mx', layout=widg.Layout(width='95%', grid_area='scanning_set1'), **ali)
step_ma       = widg.BoundedFloatText(value=0, step = 0.01, description='', min=0, disabled=False, layout=widg.Layout(width='75%', grid_area='beam_set7'))

matrix_list   = pty.load_mappings()
matrix        = widg.Dropdown(options=matrix_list, value=matrix_list[4], description='Scanning matrix', layout=widg.Layout(width='94%', grid_area='scanning_set2'), **ali)
dwell_time    = widg.SelectionSlider(options=pty.load_dwelltimes(), value=10, description='Dwell time (μs)', layout=widg.Layout(width='95%', grid_area='scanning_set3'), **ali)

### Detection
camera_set    = widg.Button(description='Detection',layout=widg.Layout(width='95%', grid_area='camera_set'),style=widg.ButtonStyle(button_color='#3b446b', font_weight= 'bold',font_size= '16px',text_color='white'),disabled = False)
cl_name   = widg.Label(value = 'Nominal CL (cm)',layout=widg.Layout(width='95%', grid_area='cl_name'),)
cl            = widg.ToggleButtons(options=pty.load_cameralengths(aperture, "nominal"), value=8, description='', layout=widg.Layout(width='95%', grid_area='cl_set1'), **ali3)

camera_name   = widg.Label(value = 'Detector', layout=widg.Layout(width='94%', grid_area='camera_name'),)
camera        = widg.Dropdown(options=pty.load_detectors(), description='', layout=widg.Layout(width='93%', grid_area='camera_set1'))
restr_name    = widg.Label(value = 'PAAR',layout=widg.Layout(width='350px', grid_area='restr_name'))
restr         = widg.ToggleButtons(options=[('.',False), ('',True)], value = False, description='',icons = ['ban','check'], layout=widg.Layout(width='95%', grid_area='camera_set2'),style = {'description_width': '80px','button_width': '48%', 'font_weight': 'bold'}, button_style='')
binning_name  = widg.Label(value = 'Binning',layout=widg.Layout(width='95%', grid_area='binning_name'))
binning        = widg.ToggleButtons(options=[('',1), ('2',2), ('4',4), ('8',8)], value=1, description='', icons = ['ban','','','',''], layout=widg.Layout(width='95%', grid_area='camera_set3'), **ali3)
camera_set6    = widg.Button(description='Post-acquisition treatments (ITR)',layout=widg.Layout(width='95%', grid_area='camera_set6'),style=widg.ButtonStyle(button_color='white', font_size= '16px',text_color='black'),disabled = False)
padding       = widg.SelectionSlider(options=[('none',1), ('double',2), ('triple',3), ('quadruple',4), ('quintuple',5)], value=1, description='Padding', continuous_update=False, orientation='horizontal', readout=True, layout=widg.Layout(width='95%', grid_area='camera_set4'), **ali)
pattern_resto = widg.SelectionSlider(options=[('none',1), ('double',2), ('triple',3), ('quadruple',4), ('quintuple',5)], value=1, description='Pattern recovery', continuous_update=False, orientation='horizontal', readout=True, layout=widg.Layout(width='95%', grid_area='camera_set5'), **ali)

aperture_res  = widg.Label(value = f'Semi-angle (mrad) '+ str("{:.1f}".format(pty.get_angle(aperture.value))),      layout=widg.Layout(width='auto', grid_area='sidebar2'))
aperture_res2 = widg.Label(value = f'corr. '            + str("{:.2f}".format(pty.get_angle_corr(aperture.value))), layout=widg.Layout(width='auto', grid_area='sidebar5'))
aperture.observe(show_probe_angle, names='value')  
aperture.observe(show_corrprobe_angle, names='value')   

### Visualisation
visual_set = widg.Button(description='Visualisation',layout=widg.Layout(width='95%', grid_area='visual_set'),style=widg.ButtonStyle(button_color='white', font_weight= 'bold',font_size= '16px',text_color='black'),disabled = False)
name1      = widg.Button(description='Scale (%)',layout=widg.Layout(width='95%', grid_area='name1'),style=widg.ButtonStyle(button_color='white', font_weight= 'bold',text_color='black'), disabled = False)
graph_size = widg.IntSlider(value=100,min=75,max=125,step=5, description='', layout=widg.Layout(width='95%', grid_area='gr_size2'), button_style='primary',disabled=False,)

### Layout
controls = widg.GridBox(children=[logo, method, beam_energy, beam_set, aperture, probe_size, defocus, scanning_set, mag, matrix, dwell_time, cl, camera_set, camera, restr_name, restr, binning_name,
                                  binning, aperture_res, aperture_res2, graph_size, name1, visual_set, padding, pattern_resto, camera_set6, probe_size_ma, aperture_ma, step_ma,cl_name, camera_name],
    layout=widg.Layout(width='325px', grid_template_rows='90px 40px 35px 35px 35px 35px 35px 30px 30px 35px 35px 35px 35px 35px 62px 35px 35px 35px 35px 95px 35px 35px 35px', grid_template_columns='22% 8% 30% 20% 25%', grid_template_areas='''
            "logo          logo          logo          logo          logo         "  
            "methods       methods       methods       methods       methods      "
            "beam_set      beam_set      beam_set      beam_set      beam_set     "   
            "beam_set1     beam_set1     beam_set1     beam_set1     beam_set1    "
            "beam_set4     beam_set4     beam_set4     beam_set4     beam_set4    "
            "beam_set3     beam_set3     beam_set3     beam_set3     beam_set5    "
            "beam_set2     beam_set2     beam_set2     beam_set2     beam_set6    "
            ".             sidebar2      sidebar2      sidebar2      sidebar5     "
            "scanning_set  scanning_set  scanning_set  scanning_set  scanning_set "  
            "scanning_set1 scanning_set1 scanning_set1 scanning_set1 beam_set7"
            "scanning_set2 scanning_set2 scanning_set2 scanning_set2 scanning_set2"
            "scanning_set3 scanning_set3 scanning_set3 scanning_set3 scanning_set3"
            "camera_set    camera_set    camera_set    camera_set    camera_set   "
            "camera_name   camera_set1   camera_set1   camera_set1   camera_set1  "
            "cl_name       cl_set1       cl_set1       cl_set1       cl_set1      "
            "restr_name    camera_set2   camera_set2   camera_set2   camera_set2  "
            "binning_name  camera_set3   camera_set3   camera_set3   camera_set3  "
            "camera_set6   camera_set6   camera_set6   camera_set6   camera_set6"
            "camera_set4   camera_set4   camera_set4   camera_set4   camera_set4  "
            "camera_set5   camera_set5   camera_set5   camera_set5   camera_set5  "
            ".             .             .             .             .            "
            "visual_set    visual_set    visual_set    visual_set    visual_set   "
            "name1         name1         gr_size2      gr_size2      gr_size2     "'''))

### GRAPH CONTROL
style   = {'description_width': 'initial'}
style2   = {'description_width': '200px'}
top_set = widg.Button(description='',layout=widg.Layout(width='%', grid_area='scanning_set'), style=widg.ButtonStyle(button_color='white', font_weight= 'bold',font_size= '16px',text_color='#0d48a1'),disabled = True)
style_graph = widg.ButtonStyle(button_color='#3b446b', font_weight= 'bold',font_size= '16px', text_color='white')

### PCTF
ctf_set        = widg.Button(description='Phase CTF',layout=widg.Layout(width='100%', grid_area='ctf_set'), style=style_graph, disabled = False)
ctf_xaxis_name = widg.Label(value = 'x-axis',layout=widg.Layout(width='95%', grid_area='ctf_xaxis_name'),)
ctf_xaxis      = widg.ToggleButtons(options=['ω','mrad', 'Å'], layout=widg.Layout(grid_area='ctxaxis'), style = {'button_width': '30%'}, disabled=False)
element        = widg.Dropdown(options=pty.load_elements(), description='Element (ITR)', layout=widg.Layout(width='95%', grid_area='ctf_element'))

### Sample
sample_set  = widg.Button(description='Sample',layout=widg.Layout(width='100%', grid_area='sample_set'), style=style_graph, disabled = False)
overlap_fig = widg.ToggleButtons(options=[('Geometrical', 'geom'),('Simulated: A', 'simA'),('Simulated: I', 'simI')], layout=widg.Layout(grid_area='overlap_fig'), style = {'button_width': '30%'}, disabled=False)
fov_show    = widg.BoundedFloatText(value=0.3,min=0.1,max=10,step=0.1,description='FoV (nm):', disabled=False,continuous_update=False,orientation='horizontal',readout=True,readout_format='.1f',layout=widg.Layout(grid_area='fov_show', width = '115px'),style={'description_width': '55px'})
beam_pos    = widg.BoundedIntText(value=4,min=4,max=100,step=2,description='Add beams:', disabled=False,continuous_update=False,orientation='horizontal',readout=True,readout_format='d',layout=widg.Layout(grid_area='beam_pos', width = '120px'),style={'description_width': '70px'})
red_box     = widg.Dropdown(options=[('tiny', 0.1), ('small', 0.2), ('middle', 0.3), ('large', 0.4), ('whole', 0.5)], value=0.1, description='Uniformity:', layout=widg.Layout(grid_area='red_box',width = '150px'),style={'description_width': '70px'})
box_col     = widg.ColorPicker(concise=False, description='', value='cyan', disabled=False, layout=widg.Layout(grid_area='box_col', width = '50px'))
prof_show   = widg.Checkbox(value=False, description='Show line profile', disabled=False, indent=False, layout=widg.Layout(grid_area='prof_show'))
rs_sampling = widg.Dropdown(options=[('Overlap', 'overlap'), ('Linear sampling', 'linear'), ('Areal sampling', 'areal')], description='',layout=widg.Layout(grid_area='rs_sampling', width = '115px'),style={'description_width': '0px'})

### Camera length based limitations and checks
cl_set     = widg.Button(description='Camera length based limitations and checks for ITR', layout=widg.Layout(width='100%', grid_area='cl_set'), style=style_graph, disabled = False)
check0name = widg.IntRangeSlider(value=[1,6],min=0, max=10,step=1, description='Detector coverage (α):', disabled=False, continuous_update=False, orientation='horizontal',readout=True, readout_format='d',layout=widg.Layout(grid_area='check0name', width = '100%'),style=style)
check1name = widg.BoundedIntText(value=10,min=0,max=50,step=1,description='Small angle approx. (°):', disabled=False,continuous_update=False,orientation='horizontal',readout=True,readout_format='d',layout=widg.Layout(grid_area='check1name', width = '200px'),style={'description_width': '140px'})
check2name = widg.BoundedFloatText(value=1,min=0.5,max=5,step=0.5, description='Resolution gain:', disabled=False,continuous_update=False,orientation='horizontal',readout=True, readout_format='.1f', layout=widg.Layout(grid_area='check2name', width = '200px'), style={'description_width': '140px'})
check4name = widg.IntSlider(value=70, min=0 ,max=100, step=5, description='Beam overlap (%):', disabled=False, continuous_update=False, orientation='horizontal', readout=True,readout_format='d', layout=widg.Layout(grid_area='check4name', width = '100%'),style=style)
check6name = widg.BoundedIntText(value=1,min=1,max=20,step=1, description='Overall sampling:', disabled=False,continuous_update=False,orientation='horizontal',readout=True, readout_format='d', layout=widg.Layout(grid_area='check6name', width = '200px'), style={'description_width': '140px'})

### Layout
graph_controls = widg.GridBox(children=[sample_set, ctf_set, ctf_xaxis, element, beam_pos, fov_show, cl_set, overlap_fig, red_box, box_col, check0name, check1name, check2name, check4name, check6name, ctf_xaxis_name, prof_show, rs_sampling],
        layout=widg.Layout(width='1600px', grid_template_rows='35px 35px 35px 35px 5px', grid_template_columns='4% 3.5% 14% 50px 8% 6.5% 3% 6.5% 1% 26% 14%', grid_template_areas='''
            ".  ctf_set          ctf_set       .    sample_set    sample_set   beam_pos     beam_pos     .  cl_set      cl_set      "   
            ".  ctf_xaxis_name   ctxaxis       .    overlap_fig   overlap_fig  overlap_fig  overlap_fig  .  check0name  check1name  "
            ".  ctf_element      ctf_element   .    fov_show      red_box      red_box      box_col      .  check4name  check2name  "
            ".  .                .             .    rs_sampling   .            prof_show    prof_show    .  .           check6name  "
            ".  .                .             .    .             .            .            .            .  .           .           "'''))  

def ptycho_interact(beam_energy, aperture, aperture_res, aperture_res2, probe_size, cl, matrix, defocus, mag, camera, binning, dwell_time, restr, method,
                    ctf_xaxis, element, graph_size, beam_pos, fov_show, overlap_fig, red_box, box_col, check0name, check1name, check2name, check4name, check6name, prof_show, padding, pattern_resto, rs_sampling, probe_size_ma, aperture_ma, step_ma):

    if probe_size == "user def. (pA)":
        current = probe_size_ma
    else:
        current = pty.get_current(probe_size,aperture)  
    
    if aperture == "user def. (mrad)":
        semi_angle = aperture_ma
        semi_angle_corr = aperture_ma
    else:
        semi_angle = pty.get_angle(aperture)
        semi_angle_corr = pty.get_angle_corr(aperture)

    if mag == "user def. step (A)":
        step_size_corr = step_ma/10
        fov = (matrix)*step_size_corr
    else:
        fov = pty.get_fov(mag)    
        step_size = pty.get_step_size(fov,matrix) # in nm
        step_size_corr = np.array(pty.get_step_correction())*pty.get_step_size(fov, matrix) # in nm

    beam_diameter = pty.get_beam_diameter(aperture, defocus, semi_angle_corr)
    pctf_itr = pty.get_ctf(element)
    cl_det = pty.get_cl_detector(cl, camera)
    omega_itr = np.array(pty.get_omegas())
    frame_rate = pty.get_aq_frec(dwell_time)
    wavelength = pty.get_wavelength(beam_energy)*1e12 # in pm   
    pixel_angle = pty.get_pixel_angle(cl, camera, binning)
    num_pixels, size_pixel = pty.get_detector(camera, binning)
    beam_diameter_pix = 2*semi_angle_corr/pixel_angle
    detector_cover = num_pixels/2*pixel_angle
    covered_alfas = detector_cover/semi_angle_corr
    overlap = (beam_diameter-step_size_corr)/beam_diameter*100
    if overlap < 0:
        overlap = 0  
    area_oversampling = (cons.pi*beam_diameter/2*beam_diameter/2)/(step_size_corr*step_size_corr)
    linear_oversampling = (2*beam_diameter/2)/(step_size_corr)
    e_per_scan = (dwell_time/1e6)*(current/1e12/cons.e)
    dose = ((matrix**2)*e_per_scan)/((((matrix-1)*step_size_corr)**2)*100)
    probe_window = pattern_resto*(wavelength*cl_det/100)/(size_pixel/1e6)/1000  # now in nm
    oversampling = (wavelength/1000)/(2*pixel_angle/1000*step_size_corr)
    max_defocus = (probe_window/4)/np.tan(semi_angle_corr/1000)
    z_res = wavelength/(2*np.sin(detector_cover/1000/2)*np.sin(detector_cover/1000/2))/100  # now in A
    dRssb = (wavelength/100)/(2*np.sin(2*semi_angle_corr/1000))
    
    ### ALL CAMERA LENGTHS PARAMETERS
    cl_all = pty.load_cameralengths(camera, "nominal")
    cl_eff_all = pty.load_cameralengths(camera, "effective")
    apertures = pty.load_apertures()
    pixel_covers = pty.get_pixel_covers(camera, binning)    
    pump_apertures = pty.get_pumping_apertures()
    detector_cover_all = pixel_covers*num_pixels/2

    if restr == True:
        for x in range(0,len(detector_cover_all)):
            if detector_cover_all[x] > pump_apertures[x]:
                detector_cover_all[x] = pump_apertures[x]      
        detector_pixels_all = np.round(detector_cover_all/pixel_covers,1)    
        ptycho_pixel_size_all = ((wavelength*np.array(cl_eff_all))/(detector_pixels_all*size_pixel/1e6)/1e4)/padding
    else:
        ptycho_pixel_size_all = ((wavelength*np.array(cl_eff_all))/(num_pixels/2*size_pixel/1e6)/1e4)/padding

    probe_window_all = pattern_resto*(wavelength*np.array(cl_eff_all)/100)/(size_pixel/1e6)/1000  # now in nm
    usable_probe_semi_window_all = probe_window_all/4
    detector_cover_a_all = detector_cover_all/semi_angle_corr
    max_defocus_all = (usable_probe_semi_window_all)/np.tan(semi_angle_corr/1000)
    max_defocus_all[max_defocus_all < 0] = 'nan'
    oversampling_all = (wavelength/1000)/(2*pixel_covers/1000*step_size_corr)
    z_res_all = (wavelength/(2*np.sin(detector_cover_all/1000/2)*np.sin(detector_cover_all/1000/2))/100)/padding  # now in A

    ### MICROSCOPE SCHEME
    width = 550 # in-graph setting
    det_width = 400 # in-graph setting
    reduc = 0.4 # in-graph setting
    defo = np.power(defocus,0.4)/100
    y_down = np.log(np.max(cl_all))
    ssb_cl, kolik = pty.get_cl4ssb(detector_cover_a_all, camera, "nominal")
    focusdepth = wavelength/(semi_angle_corr/1000)**2/1000
    y = -np.log(cl)*np.ones(int(num_pixels)+1)
    x = np.linspace(-det_width, det_width, int(num_pixels)+1)
    
    fig = go.Figure() 
    fig.update_xaxes(range=[-width, width], showticklabels=False,zeroline=False)
    fig.update_yaxes(range=[-y_down, reduc*y_down], showticklabels=False)
    fig.add_shape(type="rect",xref="x", yref="y",opacity=0.05, fillcolor="gray", x0=-width, y0=-y_down, x1=width, y1=reduc*y_down,line_color="gray")
    fig.add_shape(type="rect",xref="x", yref="y",opacity=0.7,  fillcolor="red",  x0=-100, y0=reduc*0.8*y_down, x1=100, y1=reduc*0.9*y_down,line_color="red")
    fig.add_trace(go.Scatter(showlegend=False, x=[-150, -2*semi_angle, None, 2*semi_angle, 150], y=[reduc*0.8*y_down,reduc*0.8*y_down,None,reduc*0.8*y_down, reduc*0.8*y_down],mode='lines', line=dict(color='black',width=7)))
    fig.add_annotation(x=-0.7*width, y=reduc*0.8*y_down, text="<b>Aperture </b>", showarrow=False, yshift=2)
    fig.add_annotation(x=-0.2*width, y=reduc*0.8*y_down, text=str(aperture), showarrow=False, yshift=-15)
    fig.add_annotation(x=0, y=-y_down,text='Net acquisition time (s) '+ str(np.round(matrix*matrix*dwell_time/1e6,1)),showarrow=False,yshift=-10)
    fig.add_annotation(x=0, y=reduc*0.96*y_down,text='λ (pm) '+ str(np.round(wavelength,2)),showarrow=False,yshift=0)

    # Beam
    fig.add_trace(go.Scatter(showlegend=False, x=[0, 2*semi_angle,  0, 0], y=[defo*y_down, reduc*0.8*y_down, reduc*0.8*y_down, defo*y_down], mode='lines',fill="toself", fillcolor="#FF7F7F", opacity=0.7,line=dict(color='#FF7F7F',width=1)))
    fig.add_trace(go.Scatter(showlegend=False, x=[0, 0, -2*semi_angle, 0], y=[defo*y_down, reduc*0.8*y_down, reduc*0.8*y_down, defo*y_down],mode='lines', fill="toself", fillcolor="red", opacity=0.7,line=dict(color='red',width=1)))
    fig.add_annotation(x=-0.05*width, y=0, ax=-0.05*width, ay=defo*y_down, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=1,arrowsize=1,arrowwidth=1,arrowcolor='black')
    fig.add_annotation(x=-0.05*width, y=defo*y_down, ax=-0.05*width, ay=0, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=1,arrowsize=1,arrowwidth=1,arrowcolor='black')
    fig.add_annotation(x=-0.3*width, y=0.05*y_down,text="Δf "+str(np.round(defocus,1))+" nm", showarrow=False)
    fig.add_annotation(x=0, y=reduc*0.5*y_down,text="Current "+str(np.round(current,1))+" pA", showarrow=True,ax=90, ay=0, yshift=0)
    fig.add_annotation(x=0, y=reduc*0.5*y_down,text="e per spot "+str(np.round(e_per_scan,1)), showarrow=True,ax=90, ay=0, yshift=-20)
    fig.add_annotation(x=-1.7*det_width, y=reduc*0.5*y_down, ax=-0.5*det_width, ay=reduc*0.5*y_down, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=3,arrowsize=2,arrowwidth=2,arrowcolor='black')
    
    # Sample
    fig.add_trace(go.Scatter(showlegend=False, x=[-0.8*width, 0.8*width], y=[0, 0], line=dict(color='magenta',width=7), opacity=0.5))
    fig.add_annotation(x=-0.7*width, y=0,text="<b>Sample</b>", showarrow=False, yshift=15, xshift =-8)
    fig.add_trace(go.Scatter(showlegend=False, x=[-np.log(fov)/20*width, np.log(fov)/20*width, np.log(fov)/20*width, -np.log(fov)/20*width, -np.log(fov)/20*width], y=[-0.01*y_down, -0.01*y_down, 0.01*y_down, 0.01*y_down, -0.01*y_down],mode='lines', fill="toself", fillcolor="black", line=dict(color='black',width=1), opacity=0.5))
    fig.add_annotation(x=0.4*width, y=0.05*y_down,text="FoV "+str(np.round(fov,2))+" nm", showarrow=False, yshift=0)
    fig.add_annotation(x=0.5*width, y=0.05*y_down,text="Dose "+str(np.round(dose,1))+" e/Å2", showarrow=False, yshift=-40)
    fig.add_annotation(x=-0.5*width, y=0.05*y_down,text="DoF "+str(np.round(focusdepth,1))+" nm", showarrow=False, yshift=-40)
    fig.add_annotation(x=1.7*det_width, y=0, ax=np.log(fov)/20*width, ay=0, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=3,arrowsize=2,arrowwidth=2,arrowcolor='black')
    
    # Detector
    fig.add_trace(go.Scatter(showlegend=False, x=x, y=y, mode='markers', marker_symbol="line-ns",marker_line_width=0.5))
    fig.add_annotation(x=-0.5*width, y=-np.log(cl),text="<b>Detector</b>", showarrow=False,align= 'left',  yshift=15)
    fig.add_annotation(x=-1.7*det_width, y=-np.log(cl), ax=-det_width, ay=-np.log(cl), xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=3,arrowsize=2,arrowwidth=2,arrowcolor='black',yshift=0)

    # Scattering
    fig.add_trace(go.Scatter(showlegend=False, x=[0, det_width, -det_width, 0], y=[defo*y_down, -np.log(cl), -np.log(cl), -np.log(cl), defo*y_down],mode='lines',fill="toself",fillcolor="gray",opacity=0.1,line=dict(color='black',width=1)))
    fig.add_trace(go.Scatter(showlegend=False, x=[0, -det_width, det_width, 0], y=[defo*y_down, -np.log(cl), -np.log(cl), -np.log(cl), defo*y_down],mode='lines',fill="toself",fillcolor="gray",opacity=0.1,line=dict(color='black',width=1)))
    
    # BF disk
    fig.add_trace(go.Scatter(showlegend=False, x=[0, det_width/covered_alfas, -det_width/covered_alfas, 0], y=[defo*y_down, -np.log(cl), -np.log(cl), -np.log(cl), defo*y_down],mode='lines',fill="toself",fillcolor="#FF7F7F",opacity=0.7,line=dict(color='#FF7F7F',width=1)))
    fig.add_trace(go.Scatter(showlegend=False, x=[0, -det_width/covered_alfas, det_width/covered_alfas, 0], y=[defo*y_down, -np.log(cl), -np.log(cl), -np.log(cl), defo*y_down],mode='lines',fill="toself",fillcolor="red",opacity=0.7,line=dict(color='#FF7F7F',width=1)))

    if method == 'ssb':
        fig.add_trace(go.Scatter(showlegend=False, x=[-width, width], y=[-np.log(ssb_cl), -np.log(ssb_cl)], opacity=0.8, line=dict(color='green',width=3)))
        fig.add_annotation(x=0*width, y=-np.log(ssb_cl),text="<b></b>", showarrow=False, align= 'left', yshift=15)
    if restr == True:
        fig.add_trace(go.Scatter(showlegend=False, x=[-250, -4*semi_angle, None, 4*semi_angle, 250], y=[-reduc*0.2*y_down,-reduc*0.2*y_down,None,-reduc*0.2*y_down, -reduc*0.2*y_down],mode='lines', line=dict(color='black',width=7)))
        fig.add_annotation(x=-0.35*width, y=-reduc*0.2*y_down,text="<b>PAAR</b>", showarrow=False,align= 'left', yshift=-15)
    
    # Cover
    fig.add_annotation(x=0, y=-np.log(cl), ax=det_width, ay=-np.log(cl), xref='x',yref='y',axref='x',ayref='y', text='', showarrow=True,arrowhead=3,arrowsize=1,arrowwidth=1,arrowcolor='black')
    fig.add_annotation(x=det_width,y=-np.log(cl),  ax=0, ay=-np.log(cl), xref='x',yref='y',axref='x',ayref='y', text='', showarrow=True,arrowhead=3,arrowsize=1,arrowwidth=1,arrowcolor='black')
    fig.add_annotation(x=det_width/2, y=-np.log(cl), text=str(np.round(detector_cover,1)) + " mrad or " + str(np.round(covered_alfas,1))+"α", showarrow=False, yshift=15, xshift=0)
    
    # CLs
    xx = 0
    for x in cl_all:
        if xx == 0:
            fig.add_annotation(x=-0.7*width, y=-np.log(x),text="Nominal CL", showarrow=False, yshift=50)
            fig.add_annotation(x=-0.7*width, y=-np.log(x),text="(cm)", showarrow=False, yshift=35)
            fig.add_annotation(x= 0.7*width, y=-np.log(x),text="Effective CL", showarrow=False, yshift=50)
            fig.add_annotation(x= 0.7*width, y=-np.log(x),text="(cm)", showarrow=False, yshift=35)
        fig.add_trace(go.Scatter(showlegend=False, x=[-width, width], y=[-np.log(x), -np.log(x)], opacity=0.3, line=dict(color='gray', width=1)))
        fig.add_annotation(x=-0.9*width, y=-np.log(x), text=str(x), showarrow=False, yshift=8)
        fig.add_annotation(x=0.85*width, y=-np.log(x), text=str(np.round(cl_eff_all[xx],1)), showarrow=False, yshift=8)
        xx +=1
        
    fig.add_annotation(x=width, y=-np.log(cl_all[0]), ax=width, ay=-np.log(cl_all[-1]), xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=0,arrowsize=2,arrowwidth=2,arrowcolor='gray',yshift=0)
    fig.add_annotation(x=1.7*det_width, y=-(np.log(cl_all[0])+np.log(cl_all[-1]))/2,ax=width, ay=-(np.log(cl_all[0])+np.log(cl_all[-1]))/2, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=3,arrowsize=2,arrowwidth=2,arrowcolor='black')
    fig.update_xaxes(title_text="")
    fig.update_layout(plot_bgcolor='white',width=4.1*graph_size, height=7.2*graph_size, margin = dict(l=0.45*graph_size, r=0.45*graph_size, t=0.0*graph_size, b=0))

    ### SAMPLE PLANE
    match overlap_fig:  
        case 'geom':
            wid = np.linspace(-beam_pos/2,beam_pos/2,beam_pos+1)*step_size_corr
            yyy = np.append(np.linspace(0,overlap,100),200)
            
            fig1 = go.Figure() 
            fig1.update_xaxes(range=[-fov_show/2, fov_show/2], showgrid=False, showline=True, mirror=True, ticks='inside',linecolor='black',gridcolor='lightgrey',title_font_color="#000000", title_text="Sample plane (nm)",zeroline=False)
            fig1.update_yaxes(range=[-fov_show/2, fov_show/2], showgrid=False, showline=True, mirror=True, ticks='',linecolor='black',gridcolor='lightgrey',title_font_color="#000000", showticklabels=False)
                           
            for x in range(len(wid)):    
                fig1.add_trace(go.Scatter(showlegend=False, x=wid, y=np.ones(len(wid))*wid[x], marker_color='black'))
                for y in range(len(wid)):  
                    fig1.add_shape(type="circle",xref="x", yref="y", opacity=0.1, fillcolor="#FF7F7F",name=False, x0=wid[x]-beam_diameter/2, y0=wid[y]-beam_diameter/2, x1=wid[x]+beam_diameter/2, y1=wid[y]+beam_diameter/2, line_color="red")
            
            fig1.add_annotation(x=-1*step_size_corr, y=-2*step_size_corr, ax=-2*step_size_corr, ay=-2*step_size_corr, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='red')
            fig1.add_annotation(x=-2*step_size_corr, y=-1*step_size_corr, ax=-2*step_size_corr, ay=-2*step_size_corr, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='red')
            fig1.add_annotation(x=2*step_size_corr-0.75*beam_diameter/2, y=-2*step_size_corr-0.75*beam_diameter/2, ax=2*step_size_corr, ay=-2*step_size_corr,xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='blue')
            fig1.add_annotation(x=2*step_size_corr+0.75*beam_diameter/2, y=-2*step_size_corr+0.75*beam_diameter/2, ax=2*step_size_corr, ay=-2*step_size_corr,xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='blue')
            fig1.add_trace(go.Scatter(showlegend=True, x=[-100], y=[-100],marker_size=12, marker_color='red', name='ΔR '+str(np.round(10*step_size_corr,3))+' Å'))    
            fig1.add_trace(go.Scatter(showlegend=True, x=[-100], y=[-100],marker_size=12, marker_color='blue', name='Probe ⌀ '+str(np.round(10*beam_diameter,2))+' Å'))   

            match method:  
                case 'ssb':
                    fig1.add_trace(go.Scatter(showlegend=True, x=(0,0), y=(0,0),marker_size=12, marker_color='green', name= '<b>ΔR_SSB ' + str(np.round(dRssb,3))+' Å<b>', opacity = 0))  
                    fig1.update_layout(width=3.15*graph_size, height=3.9*graph_size, plot_bgcolor='white', margin = dict(l=0.65*graph_size, r=0.01*graph_size, t=0.8*graph_size, b=0.7*graph_size),
                                       legend = dict(orientation="v",yanchor="bottom",y=1.01, xanchor="right",x=1), title  = {'text': "Sample",'y': 0.87, 'x': 0.23,'xanchor': 'left','yanchor': 'top'})
                case 'iterative':
                    match rs_sampling:
                        case 'overlap':
                            fig1.add_trace(go.Scatter(x=(0,0), y=(0,0), name='<b>Overlap '+str(np.round(overlap,1))+' %<b>', showlegend=True, opacity = 0))
                        case 'linear':
                            fig1.add_trace(go.Scatter(x=(0,0), y=(0,0), name='<b>Linear sampl. '+str(np.round(linear_oversampling,1))+'<b>', showlegend=True, opacity = 0))
                        case 'areal':
                            fig1.add_trace(go.Scatter(x=(0,0), y=(0,0), name='<b>Area sampl. '+str(np.round(area_oversampling,1))+'<b>', showlegend=True, opacity = 0))

                    fig1.update_layout(width=2.9*graph_size, height=3.7*graph_size, plot_bgcolor='white', margin =dict(l=0.2*graph_size, r=0.1*graph_size, t=0.8*graph_size, b=0),
                                       legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="right",x=1), title={'text': "Sample",'y': 0.87, 'x': 0.1,'xanchor': 'left','yanchor': 'top'})
    
        case overlap_fig if overlap_fig in ['simI', 'simA']:
            if abtem == True:
                sampling= 0.05 # sampling of the simulated potential in A
                sys.stdout = io.StringIO()  # create a text trap and redirect stdout
                probe = Probe(sampling = sampling, extent = 2*beam_diameter*10, energy = beam_energy*1e3, semiangle_cutoff = semi_angle_corr, defocus = defocus*10) # sampling=sampling, extent=A , energy=beam*1e3eV, semiangle_cutoff=mrad, defocus=A)
                probe_simul = probe.build().intensity().compute().array
                
                if overlap_fig == "simI":
                    probe_simul = np.square(probe_simul)
                    probe_simul = np.abs(probe_simul)
                elif overlap_fig == "simA":
                    probe_simul = np.abs(probe_simul)

                sys.stdout = sys.__stdout__    # now restore stdout function
                x_pix = int(step_size_corr*10/sampling) # step size from nm to A
                field = np.zeros([probe_simul.shape[0]+(beam_pos)*x_pix, probe_simul.shape[1]+(beam_pos)*x_pix])
                cen = int(probe_simul.shape[0]/2)
           
                for i in range(0,beam_pos+1):
                    for j in range(0,beam_pos+1):
                        xx = x_pix*i
                        xy = x_pix*j
                        field[xy:probe_simul.shape[0]+xy,xx:probe_simul.shape[0]+xx]=field[xy:probe_simul.shape[0]+xy,xx:probe_simul.shape[0]+xx]+probe_simul
        
                field_size =int(field.shape[0]) 
                field_cen = int(field.shape[0]/2)
                middle = field[int(field_cen-(x_pix*(beam_pos)*red_box)):int(field_cen+(x_pix*(beam_pos)*red_box)),int(field_cen-(x_pix*(beam_pos)*red_box)):int(field_cen+(x_pix*(beam_pos)*red_box))]
                uniformity = (1-(np.max(middle)-np.min(middle))/(np.max(field)-np.min(field)))*100
    
                fig1 = go.Figure() 
                fig1.add_trace(px.imshow(field).data[0])
                fig1.add_shape(type="rect",x0= field_cen-red_box*field_size, y0=field_cen-red_box*field_size, x1= field_cen+red_box*field_size, y1=field_cen+red_box*field_size,line=dict(color=box_col))
                fig1.update_traces(dict(showscale=False, coloraxis=None, colorscale='inferno'), selector={'type':'heatmap'})
                fig1.add_trace(go.Scatter(x=np.array(probe_window/4), y=np.array(probe_window/4), name='Uniformity '+str(np.round(uniformity,1))+' %', showlegend=True, opacity = 0))
            
                fig1.update_xaxes(range=[0, field_size-1], mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000", title_text="Sample plane (nm)", showgrid=False, showticklabels=True, 
                                  tickvals = [0, field.shape[0]/2, field.shape[0]-1], ticktext = [0, np.round((field.shape[0]/2)*sampling,1), np.round((field.shape[0]-1)*sampling,1)])
                fig1.update_yaxes(range=[0, field_size-1], showticklabels=False)
                fig1.update_layout(width=3.2*graph_size, height=3.9*graph_size, margin =dict(l=0.5*graph_size, r=0.1*graph_size, t=0.9*graph_size, b=0.55*graph_size),
                                   legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="right",x=0.8), title={'text':"Illumination",'y':0.90,'x':0.4,'xanchor':'left','yanchor':'top'})
            else:
                fig1 = go.Figure() 
                fig1.update_layout(title={'text': "abTEM not available",'y': 0.98, 'x': 0.14,'xanchor': 'left','yanchor': 'top'},
                                   width=3.2*graph_size, height=3.9*graph_size, margin =dict(l=0.5*graph_size, r=0.2*graph_size, t=0.9*graph_size, b=0.55*graph_size))

    ### DETECTOR PLANE
    fig2 = go.Figure() 
    fig2.add_shape(type="circle",xref="x", yref="y",opacity=0.5, fillcolor="#FF7F7F", x0=(num_pixels+1)/2-beam_diameter_pix/2, y0=(num_pixels+1)/2-beam_diameter_pix/2, x1=(num_pixels+1)/2+beam_diameter_pix/2, y1=(num_pixels+1)/2+beam_diameter_pix/2,line_color="red")
    fig2.add_shape(type="rect",xref="x", yref="y",opacity=0.5,  fillcolor="#f0f921", x0=0.5, y0=0.5, x1=1.5, y1=1.5,line_color="#000004") 
    fig2.add_annotation(x=(num_pixels+1)/2-beam_diameter_pix/2, y=(num_pixels+1)/2, ax=(num_pixels+1)/2+beam_diameter_pix/2, ay=(num_pixels+1)/2, xref='x',yref='y',axref='x',ayref='y',text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='black')
    fig2.add_annotation(x=(num_pixels+1)/2+beam_diameter_pix/2, y=(num_pixels+1)/2, ax=(num_pixels+1)/2-beam_diameter_pix/2, ay=(num_pixels+1)/2, xref='x',yref='y',axref='x',ayref='y', text='', showarrow=True,arrowhead=2,arrowsize=2,arrowwidth=1,arrowcolor='black')
    fig2.add_annotation(x=(num_pixels+1)/2, y=(num_pixels+1)/2, text=str(np.round(beam_diameter_pix,1))+" pix", showarrow=False, yshift=10)
    fig2.add_annotation(x=1, y=1, text=str(np.round(size_pixel,2))+" μm ≈ " +str(np.round(pixel_angle,4))+" mrad", showarrow=False, xshift=70+(50/np.sqrt(num_pixels)), yshift=10+(50/np.sqrt(num_pixels)))
    fig2.add_annotation(x=(num_pixels+1)/2, y=(num_pixels+1)/2, text="BF disk", showarrow=False, yshift=-15, font=dict(family="calibri", size=18, color="#FF7F7F"))
    fig2.update_xaxes(title_text="Detector pixel array", range=[0.5, num_pixels+0.5], tickvals = [1, num_pixels/2+0.5, num_pixels],
                      ticktext = [1, num_pixels/2, num_pixels], showticklabels=True, showgrid=True, mirror=True, ticks='inside', showline=True, linecolor='black', gridcolor='lightgrey', title_font_color="#000000") 
    fig2.update_yaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000",title_text="Cover angle (mrad)", showticklabels=True, showgrid=True,
                      range=[0.5, num_pixels+0.5], tickvals = [1, num_pixels/2+0.5, num_pixels], ticktext = [str(np.round(-detector_cover,1)), "0", str(np.round(detector_cover,1))])
    fig2.update_layout(width=3.45*graph_size, height=4.7*graph_size, margin =dict(l=0.65*graph_size, r=0.25*graph_size, t=1.9*graph_size, b=0),
                       title={'text': "Detector",'y':0.65, 'x': 0.44,'xanchor': 'left','yanchor': 'top'}, plot_bgcolor='white', legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="left",x=0.1))

    match method:  
        case 'ssb':
            ### CAMERA LENGTH GRAPH
            fig4 = make_subplots(specs=[[{"secondary_y": True}]])
            fig4.add_trace(go.Scatter(showlegend=False,x=cl_all, y=detector_cover_all,  marker_color='black'), secondary_y=False)
            fig4.add_trace(go.Scatter(showlegend=False,x=cl_all, y=detector_cover_a_all,marker_color='black'), secondary_y=True)
            fig4.add_trace(go.Scatter(x=np.array(ssb_cl), y=np.array(kolik),marker_size=12, marker_color='green', name = "Maximal CL"), secondary_y=True)  
            fig4.add_trace(go.Scatter(showlegend=False,x=[np.min(cl_all)/1.5,np.array(cl)], y=[detector_cover, detector_cover], mode='lines',marker_color='gray'), secondary_y=False)
            fig4.add_trace(go.Scatter(showlegend=False,x=[np.array(cl),np.array(cl)], y=[0, np.array(covered_alfas)], mode='lines',marker_color='gray'), secondary_y=True)
            fig4.add_trace(go.Scatter(showlegend=False,x=[np.array(cl),np.max(cl_all)*1.5], y=[np.array(covered_alfas), np.array(covered_alfas)], mode='lines',marker_color='gray'), secondary_y=True)
            fig4.add_trace(go.Scatter(showlegend=False,x=np.array(cl), y=np.array(covered_alfas), marker_size=12, marker_color='red', name = str(np.round(detector_cover,1))+ " mrad; "+str(np.round(covered_alfas,2))+ " α"), secondary_y=True)  
            fig4.add_annotation(x=np.log10(np.max(cl_all)), y=detector_cover, text=str(np.round(covered_alfas,1)), showarrow=False, xshift=15, yshift=+10, secondary_y=False)
            fig4.add_annotation(x=np.log10(np.min(cl_all)), y=detector_cover, text=str(np.round(detector_cover,1)), showarrow=False, xshift=-15, yshift=+10, secondary_y=False)
            fig4.update_layout(xaxis=dict(tickmode = 'array', tickvals = [1, num_pixels/4, num_pixels/2, 3*num_pixels/4, num_pixels]))
            fig4.update_xaxes(range=[np.log10(np.min(cl_all)/1.5), np.log10(np.max(cl_all)*1.5)], title_text="Nominal camera length (cm)", type="log", tickvals = cl_all, mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig4.update_yaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig4.update_yaxes(title_text=" Cover angle (mrad)", range=[0, 1.1*np.max(detector_cover_all)], secondary_y=False)
            fig4.update_yaxes(title_text=" Cover angle (α)", range=[0, 1.1*np.max(detector_cover_a_all)], showgrid=False, secondary_y=True)
            fig4.update_layout(title={'text': "Camera length",'y':0.95, 'x':0.17,'xanchor': 'left','yanchor': 'top'}, legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="right",x=0.95), plot_bgcolor='white',
                               width=3.61*graph_size, height=3.4*graph_size, margin =dict(l=0.3*graph_size, r=0.25*graph_size, t=0.3*graph_size, b=0.3*graph_size))
            
            ### SSB-PCTF
            omega, pctf = pty.get_ssb_ctf()
            xx = wavelength/(np.sin(semi_angle_corr*omega/1000))/100 # pitch size
            
            fig5 = go.Figure() 
            fig5.update_yaxes(title_text="Transfer (-)")
            match ctf_xaxis:
                case 'ω':
                    fig5.add_trace(go.Scatter(showlegend=True, x=omega, y=pctf, marker_color='red', name='For all apertures'))   
                    fig5.update_xaxes(title_text="Spatial frequency (ω)", range=[0, 2], zeroline=False)
                case 'mrad':
                    for x in apertures:
                        if x == apertures[0]:
                            fig5.add_trace(go.Scatter(showlegend=True, x=pty.get_angle_corr(x)*omega, y=pctf, marker_color='gray', name='Others'))
                        else:
                            fig5.add_trace(go.Scatter(showlegend=False, x=pty.get_angle_corr(x)*omega, y=pctf, marker_color='gray'))
                    fig5.add_trace(go.Scatter(showlegend=True, x=semi_angle_corr*omega, y=pctf, marker_color='red', name='Selected aperture'))
                    fig5.update_xaxes(title_text="Spatial frequency (mrad)", range=[0, 2*semi_angle_corr], zeroline=False)
                case 'Å':
                    for x in apertures:
                        d = wavelength/(np.sin(pty.get_angle_corr(x)*omega/1000))/100  # Full pitch size
                        if x == apertures[0]:
                            fig5.add_trace(go.Scatter(showlegend=True, x=d, y=pctf, marker_color='gray', name='Others'))
                        else:
                            fig5.add_trace(go.Scatter(showlegend=False, x=d, y=pctf, marker_color='gray'))
                    fig5.add_trace(go.Scatter(showlegend=True, x=xx, y=pctf, marker_color='red', name='Selected aperture'))
                    fig5.update_xaxes(title_text="Spacing (Å)", range=[-0.5, 2], type="log", zeroline=False)
        
            fig5.update_xaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig5.update_yaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig5.update_layout(width=3.5*graph_size, height=2.2*graph_size, margin = dict(l=0.3*graph_size, r=0.3*graph_size, t=0.5*graph_size, b=0.4*graph_size), plot_bgcolor='white',
                               title={'text': "Phase CTF",'y':0.99, 'x':0.42,'xanchor': 'left','yanchor': 'top'},legend=dict(orientation="h",yanchor="bottom",y=1.01,xanchor="right",x=0.95))
             
        case 'iterative':
            ### ITR-PCTF
            pctf_norm = pctf_itr/np.max(pctf_itr)
            fig5 = go.Figure() 
            fig5.update_yaxes(title_text="Transfer (-)")
            match ctf_xaxis:  
                case 'ω':
                    fig5.add_trace(go.Scatter(showlegend=True, x=omega_itr, y= pctf_norm, marker_color='red', name='For all apertures'))
                    fig5.update_xaxes(title_text="Spatial frequency (ω)", range=[0, 6], zeroline=False)
                    fig5.update_yaxes(range=[0, 1.1])
                case 'mrad':  
                    for x in apertures:
                        if x == apertures[0]:
                            fig5.add_trace(go.Scatter(showlegend=True, x=pty.get_angle_corr(x)*omega_itr, y=pctf_norm, marker_color='gray', name='Others'))
                        else:
                            fig5.add_trace(go.Scatter(showlegend=False, x=pty.get_angle_corr(x)*omega_itr, y=pctf_norm, marker_color='gray'))
                    fig5.add_trace(go.Scatter(showlegend=True, x=semi_angle_corr*omega_itr, y=pctf_norm, marker_color='red', name='Selected aperture'))
                    fig5.update_xaxes(title_text="Spatial frequency (mrad)", range=[0, 6*semi_angle_corr], zeroline=False)
                case 'Å':
                    for x in apertures:
                        d = wavelength/(np.sin(pty.get_angle_corr(x)*omega_itr/1000))/100
                        if x == apertures[0]:
                            fig5.add_trace(go.Scatter(showlegend=True, x=d, y=pctf_norm, marker_color='gray', name='Others'))
                        else:
                             fig5.add_trace(go.Scatter(showlegend=False, x=d, y=pctf_norm, marker_color='gray'))
                    xx = wavelength/(np.sin(semi_angle_corr*omega_itr/1000))/100
                    fig5.add_trace(go.Scatter(showlegend=True, x=xx, y=pctf_norm, marker_color='red', name='Selected aperture'))
                    fig5.update_xaxes(title_text="Spacing (Å)",range=[-1, 2], type="log", zeroline=False)
                     
            fig5.update_xaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig5.update_yaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000")
            fig5.update_layout(width=3.5*graph_size, height=2.2*graph_size, margin = dict(l=0.3*graph_size, r=0.3*graph_size, t=0.5*graph_size, b=0.4*graph_size),
                               title={'text': "Phase CTF",'y':0.99, 'x':0.42,'xanchor': 'left','yanchor': 'top'}, legend=dict(orientation="h",yanchor="bottom",y=1.01,xanchor="left",x=0), plot_bgcolor='white')

            ### PROBE WINDOW
            match overlap_fig:
                case 'geom': 
                    if beam_diameter < probe_window/2:
                        color  = "green"
                    elif beam_diameter < probe_window:
                        color  = "orange"
                    else:
                        color  = "red"

                    opacity =[0.2, 0.2, 0.2, 0.2,  0.2, 0.2, 0.2, 0.4]
                    xcoef =  [8,   6,   5,   4.25, 3.5, 3,   2.5, 2]

                    fig3 = go.Figure() 
                    fig3.add_shape(type="rect",xref="x", yref="y",opacity=0.3, fillcolor="#6F6F6F", x0=probe_window/4, y0=probe_window/4, x1=3*probe_window/4, y1=3*probe_window/4,line_color="#6F6F6F")
                    fig3.add_trace(go.Scatter(x=np.array(probe_window/2), y=np.array(probe_window/2), name='<b>Maximal Δf '+str(np.round(max_defocus,1))+' nm<b>', showlegend=True, marker_color=color, opacity = 0))

                    for i in range(0, len(opacity)):
                        fig3.add_shape(type="circle",xref="x", yref="y", opacity=opacity[i], fillcolor=color, x0=probe_window/2-beam_diameter/xcoef[i], y0=probe_window/2-beam_diameter/xcoef[i], 
                                       x1=probe_window/2+beam_diameter/xcoef[i], y1=probe_window/2+beam_diameter/xcoef[i], line_color=color)
                    
                    fig3.update_xaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000", 
                                      title_text="Probe window (nm)", range=[0, probe_window], tickvals = [0, probe_window/4, probe_window/2, 3*probe_window/4, probe_window], ticktext = [0, np.round(probe_window/4,2),np.round(probe_window/2,2),np.round(3*probe_window/4,2),np.round(probe_window,2)])
                    fig3.update_yaxes(mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000",
                                      range=[0, probe_window], tickvals = [0, probe_window/4, probe_window/2, 3*probe_window/4, probe_window], showticklabels=False)
                    fig3.update_layout(width=3.2*graph_size, height=4.0*graph_size, margin =dict(l=0.5*graph_size, r=0, t=0.8*graph_size, b=0.75*graph_size), plot_bgcolor='white',
                                       legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="right",x=0.8),title={'text':"Probe",'y':0.92,'x':0.48,'xanchor':'left','yanchor':'top'})  

                case overlap_fig if overlap_fig in ['simI', 'simA']:
                    if abtem == True:
                        sampling= 0.1  # sampling of the simulated potential in A
                        probe = Probe(sampling = sampling, extent = 2*probe_window*10, energy = beam_energy*1e3, semiangle_cutoff = semi_angle_corr, defocus = defocus*10)
                        # probe = Probe(sampling=sampling, extent= A , energy=beam*1e3 eV, semiangle_cutoff = mrad, defocus= A)
                        probe_simul = probe.build().intensity().compute().array
                
                        if overlap_fig == "simI":
                            probe_simul = np.square(probe_simul)
                            probe_simul = np.abs(probe_simul)
                        elif overlap_fig == "simA":
                            probe_simul = np.abs(probe_simul)
                        
                        cen2 = probe_simul.shape
                        sirkaA = cen2[0]*sampling
                        sirkaB = np.round(probe_window,2)*10/sampling
                        just_probe_window = probe_simul[int(cen2[0]/2)-int(sirkaB/2):int(cen2[0]/2)+int(sirkaB/2), int(cen2[0]/2)-int(sirkaB/2):int(cen2[0]/2)+int(sirkaB/2)]
                        int_tot = np.sum(just_probe_window)/np.sum(probe_simul)*100
                        cross_section = probe_simul[int(cen2[0]/2),:]
                        cross_section = (cross_section-np.min(cross_section))/np.max(cross_section)

                        fig3 = go.Figure() 
                        fig3.add_trace(px.imshow(probe_simul).data[0])
                        if prof_show == True:
                            fig3.add_trace(go.Scatter(x=np.linspace(0,int(cen2[0])-1,len(cross_section)), y=int(cen2[0]/4)+cross_section*int(cen2[0]/2), showlegend=False, marker_color="white", opacity = 0.7))

                        fig3.add_trace(go.Scatter(x=np.array(probe_window/4), y=np.array(probe_window/4), name='Probe covered '+str(np.round(int_tot,1))+' %', showlegend=True, opacity = 0))
                        fig3.add_shape(type="rect",x0= cen2[0]/2-sirkaB/2, y0=cen2[0]/2-sirkaB/2, x1= cen2[1]/2+sirkaB/2, y1=cen2[1]/2+sirkaB/2, line=dict(color="red"))
                        fig3.update_traces(dict(showscale=False, coloraxis=None, colorscale='inferno'), selector={'type':'heatmap'})
                        fig3.update_xaxes(range=[0, 2*sirkaB-1], mirror=True,ticks='inside',showline=True,linecolor='black',gridcolor='lightgrey',title_font_color="#000000", title_text="Probe window (nm)", showgrid=False, showticklabels=True, tickvals = [sirkaB/2, sirkaB, 3*sirkaB/2], ticktext = [0, np.round(sirkaB/200,2), np.round(sirkaB/100,2)])
                        fig3.update_yaxes(range=[0, 2*sirkaB-1],showticklabels=False)
                        fig3.update_layout(width=3.0*graph_size, height=3.9*graph_size, margin =dict(l=0.4*graph_size, r=0.1*graph_size, t=0.9*graph_size, b=0.55*graph_size),
                                           legend=dict(orientation="v",yanchor="bottom",y=1.01,xanchor="right",x=0.8),title={'text':"Probe",'y':0.9,'x':0.4,'xanchor':'left','yanchor':'top'})
                    else:
                        fig3 = go.Figure() 
                        fig3.update_layout(title={'text': "abTEM not available",'y': 0.98, 'x': 0.14,'xanchor': 'left','yanchor': 'top'})
                        fig3.update_layout(width=2.7*graph_size, height=3.9*graph_size, margin =dict(l=0.1*graph_size, r=0.1*graph_size, t=0.9*graph_size, b=0.55*graph_size))

            ### CAMERA LENGTH TABLE
            dictionary = {}
            tab = np.array([cl_all, np.round(ptycho_pixel_size_all,2), np.round(z_res_all,2), np.round(detector_cover_all,1) , np.round(detector_cover_a_all,1), 
                            np.round(probe_window_all,2), np.round(max_defocus_all,1), np.round(oversampling_all,1)])
            
            for i in range(0,len(cl_eff_all)):
                button_style = 'success'
                icons=['','','','','','','','','']
                data = tab[:,int(i)] # 0.cl, 1. ptycho pix xy, 2. ptycho pix z, 3.det cov, 4.det cov a, 5.probe window restored, 6. max defocus, 7.oversampling,
   
                if cl == data[0]:
                    icons[0]= "hand-point-left"
                 
                if data[1] > step_size_corr*10/check2name:  # check2name = 'Ptycho pixel < step size'
                    icons[1]= "bell"
                    button_style = 'warning'
                    
                if data[3] > 1000*np.radians(check1name): # check1name = 'Low anlge approximation'
                    icons[3]= "bell"
                    button_style = 'warning' 
                    
                if data[4] < check0name[0] or data[4] > check0name[1]: #  'Detector cover'
                    icons[4]= "bell"
                    button_style = 'warning'
                    
                if beam_diameter > data[5]/2:
                    icons[5]= "bell"
                    button_style = 'warning'
                    
                if data[7] < 1:       # check6name = 'Sampling > 1'    
                    icons[7]= "ban"
                    button_style = 'danger'    
                    
                if data[7] > 1 and data[6] < int(check6name): # check6name = 'Sampling > check6name'     
                    icons[7]= "bell"
                    button_style = 'warning'      

                if data[7] < pattern_resto:
                    icons[7]= "ban"
                    button_style = 'danger'  
                    
                dictionary[i] = widg.ToggleButtons(options=tuple(data), text_color= 'red', button_style=button_style, icons = icons, layout=widg.Layout(width=str(int(graph_size/100*70))+'px'),
                                                      style = {'description_width': '0px','button_width': str(int(graph_size/100*67))+'px'}, disabled=True)
            legend = widg.ToggleButtons(options=['L (cm)','∆x (Å)','∆z (Å)', 'θ (mrad)','θ (α)', 'Dψ (nm)', 'Δf (nm)','Ŝx,y'],
                                        tooltips=['Nominal camera length','Reconstucted pixel size','Minimal slice thickness for multi-slice reconstruction', 'Maximum detected angle',
                                                  'Maximum detected angle in multiplications of probe semi-angle', 'Probe window size', 'Maximum defocus to create an adequately sampled probe', 'Combined sampling'],
                                        button_style='', layout=widg.Layout(width='85px'), style = {'description_width': '0px','button_width': "80px"}, disabled=True)      
            
            # FIX here
            match len(cl_eff_all):
                case 1: 
                    cltab = widg.HBox([legend, dictionary[0]])
                case 2: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1]])
                case 3: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2]])
                case 4: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3]])
                case 5: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4]])
                case 6: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5]])
                case 7: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6]])
                case 8: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7]])
                case 9: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7], dictionary[8]])
                case 10: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7], dictionary[8], dictionary[9]])
                case 11: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7], dictionary[8], dictionary[9], dictionary[10]])
                case 12: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7], dictionary[8], dictionary[9], dictionary[10], dictionary[11]])
                case 13: 
                     cltab = widg.HBox([legend, dictionary[0], dictionary[1], dictionary[2], dictionary[3], dictionary[4], dictionary[5], dictionary[6], dictionary[7], dictionary[8], dictionary[9], dictionary[10], dictionary[11], dictionary[12]])
                
            cltab = widg.VBox([widg.Label('CAMERA LENGTH GUIDE'), cltab])
            cltab.layout = widg.Layout(border='solid 0px gray',margin='0px 0px 0px 15px', padding='5px 5px 5px 5px')

    ### SHOWING
    left  = widg.VBox([go.FigureWidget(fig5),go.FigureWidget(fig2)])
    match method: 
        case 'ssb':
            check_width = '220px'
            check_descr_width = '120px'
            check1_ssb = widg.Valid(value= bool(step_size_corr*10 < dRssb), description='Real-space sampling', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True)
            check2_ssb = widg.Valid(value= bool(1 < covered_alfas)        , description='Detector coverage', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True)
            check3_ssb = widg.Valid(value= bool(4 < beam_diameter_pix)    , description='Minimal BF size', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True)
            checks_ssb = widg.VBox([check1_ssb, check2_ssb,check3_ssb]) # Label('Final checks')
            checks_ssb.layout = widg.Layout(margin='100px 0px 0px 30px', padding='0px 0px 0px 0px', border='solid 0px gray') # border='dashed 1px gray'
            right = widg.VBox([go.FigureWidget(fig1), widg.HBox([go.FigureWidget(fig4), checks_ssb]) ])
          
        case 'iterative':
            check_width = '220px'
            check_descr_width = '120px'
            check1_itr = widg.Valid(value= bool(overlap > check4name), description='Beam overlap',layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True)
            check2_itr = widg.Valid(value= bool(step_size_corr*10 > (wavelength*cl_det)/(num_pixels*size_pixel/1e6)/1e4), description='Resolution gain', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True)
            check3_itr = widg.Valid(value= bool(beam_diameter/2 < probe_window/2), description='Probe window', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True) 
            check4_itr = widg.Valid(value= bool(oversampling > 1), description='Combined sampling', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True) 
            check5_itr = widg.Valid(value= bool(oversampling > pattern_resto), description='Pattern recovery', layout=widg.Layout(width=check_width), style = {'description_width': check_descr_width}, disabled=True) 
            checks_itr = widg.HBox([widg.VBox([check1_itr, check2_itr]), widg.VBox([check3_itr, check4_itr]), widg.VBox([check5_itr])]) # Label('Final checks')
            checks_itr.layout = widg.Layout(margin='0px 0px 0px 5px', padding='0px 0px 0px 0px', border='solid 0px gray') # border='dashed 1px gray'
            right  = widg.VBox([widg.HBox([go.FigureWidget(fig1),go.FigureWidget(fig3)]), cltab, checks_itr])
       
    total = widg.HBox([left, go.FigureWidget(fig), right])   
    total.layout = widg.Layout(border='solid 0px gray',margin='10px 10px 10px 10px', padding='0px 0px 0px 0px')            
    display(total)
    return 
    
gui = widg.interactive_output(ptycho_interact, {"beam_energy" : beam_energy, "aperture": aperture, "aperture_res": aperture_res, "aperture_res2": aperture_res2, "probe_size": probe_size, "cl": cl, "matrix": matrix, "defocus": defocus, "mag": mag,
                                                "camera": camera, "binning": binning, "dwell_time" : dwell_time, "restr": restr, "method": method, "ctf_xaxis": ctf_xaxis, "element": element, "graph_size": graph_size, "beam_pos": beam_pos,
                                                "fov_show": fov_show, "overlap_fig" :overlap_fig, "red_box": red_box, "box_col":box_col, "check0name":check0name, "check1name": check1name, "check2name": check2name, "check4name": check4name,
                                                "check6name": check6name, "prof_show":prof_show, "padding":padding, "pattern_resto":pattern_resto, "rs_sampling": rs_sampling, "probe_size_ma": probe_size_ma, "aperture_ma": aperture_ma, "step_ma": step_ma }) 

ptychoscopy = widg.VBox([top_set, widg.HBox([controls, widg.VBox([graph_controls, gui])])])